In [2]:
from IPython.display import Audio, display
from py_scripts.audio_utils import load_wav_from_source, load_audio_data, display_audio_properties, plot_waveform

# Adjustable variables
wav_source = 'tutorials/samples/cello_arco_d_sul_c_01.wav'
desired_sample_rate = None
convert_to_mono = True

# Load WAV and audio data
wav_filename = load_wav_from_source(wav_source)
audio_data, sample_rate = load_audio_data(wav_filename, desired_sample_rate, convert_to_mono)

# Display audio properties
num_channels = display_audio_properties(audio_data, sample_rate, wav_source)
# Plot waveform and get duration
duration = plot_waveform(audio_data, sample_rate, wav_filename)

# If the audio data is multi-channel, select the first channel to display
if num_channels > 1:
    audio_data = audio_data[:, 0]

# Create an audio player for the loaded file
display(Audio(audio_data, rate=sample_rate))

WAV file loaded from local path: c:\Users\egorp\Nextcloud\code\public_repos\audiospylt\tutorials\samples\cello_arco_d_sul_c_01.wav
Number of audio channels: 1
Sampling rate: 44100 Hz
WAV file loaded from tutorials/samples/cello_arco_d_sul_c_01.wav
Total duration: 8.500 seconds


In [3]:
from py_scripts.audio_utils import trim_and_fade_audio

start_time = 0.37
end_time = 0.75
add_fades = True
fade_in_duration = 0.03
fade_out_duration = 0.05
fade_in_exponent = 0.8
fade_out_exponent = 1.5

cut_audio_data, cut_duration = trim_and_fade_audio(audio_data, sample_rate, num_channels, duration, wav_filename, start_time, 
                                                   end_time, add_fades, fade_in_duration, fade_out_duration, 
                                                   fade_in_exponent, fade_out_exponent)

# Create an audio player for the loaded file
display(Audio(cut_audio_data, rate=sample_rate))

In [5]:
import numpy as np

from py_scripts.generate_wave_file import generate_wave_file

y_combined_no_nan = np.nan_to_num(cut_audio_data)

generate_wave_file(y_combined_no_nan, sample_rate, fs_target_name='44.1kHz', bit_rate=24)

# add custom_filename='my_custom_filename.wav' if needed


[2025-05-21 05:07:10] 24-bit wave file with 44.1kHz sampling rate saved successfully to: c:\Users\egorp\Nextcloud\code\public_repos\audiospylt\rendered_audio\generated_wave_file_44.1kHz_24bit_05_07_10.wav


'c:\\Users\\egorp\\Nextcloud\\code\\public_repos\\audiospylt\\rendered_audio\\generated_wave_file_44.1kHz_24bit_05_07_10.wav'

In [6]:
import plotly.graph_objects as go
from scipy.signal import spectrogram

# Compute the spectrogram data
frequencies, times, Sxx = spectrogram(cut_audio_data, fs=sample_rate, nperseg=2048, noverlap=256)

# Convert the amplitude spectrogram to dB scale
Sxx_dB = 10 * np.log10(Sxx)

# Display the spectrogram using Plotly
fig = go.Figure(data=go.Heatmap(z=Sxx_dB, x=times, y=frequencies, colorscale='Viridis', zmin=np.min(Sxx_dB), zmax=np.max(Sxx_dB)))
fig.update_layout(title="Spectrogram",
                  xaxis_title="Time (s)",
                  yaxis_title="Frequency (Hz)")

fig.show()

In [10]:
from py_scripts.dft_analysis import analyze_signal


peaks_df = analyze_signal(
        signal=cut_audio_data, 
        sr=sample_rate, 
        filename=wav_source,
        window_type='boxcar', 
        thresh_amp_low=0.002, 
        thresh_amp_high=0.0375, 
        thresh_freq_low=30, 
        thresh_freq_high=2000, 
        prominence=0.00005, 
        width=None,
        show_peaks=True, 
        show_plot=True
    )


File name: tutorials/samples/cello_arco_d_sul_c_01.wav
Duration (s): 0.38
Sampling rate (Hz): 44100

Maximum amplitude value: 0.102953
Total number of bands: 8380
Frequency resolution (Hz): 2.631579

Amplitude Threshold 1: 0.002
Amplitude Threshold 2: 0.0375
Frequency Threshold 1 (Hz): 30
Frequency Threshold 2 (Hz): 2000

Peaks:


Frequency (Hz)  Amplitude
0        73.684211   0.005356
1       136.842105   0.004395
2       223.684211   0.011307
3       297.368421   0.035448
4       371.052632   0.005977
5       442.105263   0.002880
6       447.368421   0.006474
7       521.052632   0.011020
8       594.736842   0.002818
9       818.421053   0.002759
10      894.736842   0.002141
11      965.789474   0.002436
12     1263.157895   0.002615

In [11]:
import os
from datetime import datetime

# save the DataFrame as a TSV file
filename = 'tsv/cello_single2.tsv'
try:
    peaks_df.to_csv(filename, sep='\t', index=False)
    print(f"Data saved successfully to {os.getcwd()}\\{filename} at {datetime.now()}.")
except:
    print("Error: data could not be saved.")

Data saved successfully to c:\Users\egorp\Nextcloud\code\public_repos\audiospylt\tsv/cello_single2.tsv at 2025-05-21 05:14:19.862029.
